## Data analysis: Linear model fit and volume corrected moments

In [1]:
using Random, Plots, Distributions, StatsBase, DataFrames, CSV, Plots.PlotMeasures

In [2]:
df = DataFrame(CSV.File("FISH_toShare_NoTSlabel_celldata_long_220620_simple_woMad3Outlier_withColDescription.csv"));

In [3]:
names(df);

In [4]:
df = df[:,[:sampleID,:gene,:NucleiCount,:Compartment,:CountMethod,:RNAperCell,:Cell_Length_um]];

In [5]:
# filter only for mad1WTGFP and NucleiCount = 1
dfa = subset(df, :gene => g -> g.=="mad1WTymEGFP", :NucleiCount => n -> n.==1)
# make cyto and nuc table separately.
dfcyto = subset(dfa, :Compartment=>c->c.=="Cytoplasm")
dfnuc = subset(dfa, :Compartment=>c->c.=="Nucleus")
# separate the 4 different samples
dfsN = [];dfsC = [];
samples = unique(dfa[!,:sampleID])
# add each to the vectors
for i in 1:4
    samp = samples[1]
    dftempN = subset(dfnuc, :sampleID=>S->S.==samples[i])
    dftempC = subset(dfcyto, :sampleID=>S->S.==samples[i])
    push!(dfsN,dftempN)
    push!(dfsC,dftempC)
end

In [6]:
dfsC;

If the moments I find differ from this then I know there's an issue! Let's collect the columns corresponding to the nuclear and cytoplasmic volumes and **counts** respectively.

In [7]:
names(dfsC[1])

7-element Vector{String}:
 "sampleID"
 "gene"
 "NucleiCount"
 "Compartment"
 "CountMethod"
 "RNAperCell"
 "Cell_Length_um"

In [8]:
n_vols = [dfsN[i][!,:Cell_Length_um] for i in 1:4]
c_vols = [dfsC[i][!,:Cell_Length_um] for i in 1:4]
n_ints = [dfsN[i][!,:RNAperCell] for i in 1:4]
c_ints = [dfsC[i][!,:RNAperCell] for i in 1:4];

In [9]:
Ns = [length(c_ints[i]) for i in 1:4];

For the linear model fits we use the Julia package GLM. This is a very convenient and fast way to construct linear models.

In [10]:
using GLM

Perform the linear model fits. Note in the below that our fitting parameters are stored in `npar` and `cpar` in the order `[intercept, gradient]`.

In [11]:
nlms = [lm(@formula(RNAperCell ~ Cell_Length_um), dfsN[i]) for i in 1:4]
npars = [coef(nlms[i]) for i in 1:4]
cs = hcat(npars...)[1,:]; ds = hcat(npars...)[2,:]
clms = [lm(@formula(RNAperCell ~ Cell_Length_um), dfsC[i]) for i in 1:4]
cpars = [coef(clms[i]) for i in 1:4]
as = hcat(cpars...)[1,:]; bs = hcat(cpars...)[2,:]

4-element Vector{Float64}:
 0.6037905581610079
 0.46608863627967206
 0.4796026025612281
 0.37971856092997336

A quick look at the linear model fit itself will tell us some properties of the fit.

In [12]:
clms[1]

StatsModels.TableRegressionModel{LinearModel{GLM.LmResp{Vector{Float64}}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}, Vector{Int64}}}}, Matrix{Float64}}

RNAperCell ~ 1 + Cell_Length_um

Coefficients:
─────────────────────────────────────────────────────────────────────────────
                    Coef.  Std. Error       t  Pr(>|t|)  Lower 95%  Upper 95%
─────────────────────────────────────────────────────────────────────────────
(Intercept)     -3.16679    0.240588   -13.16    <1e-36  -3.63882   -2.69475
Cell_Length_um   0.603791   0.0228683   26.40    <1e-99   0.558923   0.648658
─────────────────────────────────────────────────────────────────────────────

Now, to construct the volume corrected moments we first need to know the mean values for the volumes and intensities. Collect these from the data.

In [13]:
n_vol_avgs = [mean(n_vols[i]) for i in 1:4]
c_vol_avgs = [mean(c_vols[i]) for i in 1:4]
n_avgs = [mean(n_ints[i]) for i in 1:4]
c_avgs = [mean(c_ints[i]) for i in 1:4]

4-element Vector{Float64}:
 3.094988234996555
 2.6687301433055026
 2.9580443633353566
 2.610546234022337

Note that even the means of the cytoplasmic can vary quite significantly between the replicates. As can the observed mean cell volumes in each experiment.

We know theoretically that to first order volume corrections to the means are nil. Let's just clarify this.

In [14]:
ds

4-element Vector{Float64}:
 0.024634400218522125
 0.05869752331164149
 0.04127424654051097
 0.01671396006187003

In [15]:
vc_mean_ns = [cs[i] + n_vol_avgs[i]*ds[i] for i in 1:4]
vc_mean_cs = [as[i] + c_vol_avgs[i]*bs[i] for i in 1:4]
# vc_mean_cs = a + c_vol_avg*b

4-element Vector{Float64}:
 3.094988234996555
 2.668730143305501
 2.958044363335355
 2.610546234022334

In [16]:
μ20s = [moment(n_ints[i], 2, n_avgs[i]) for i in 1:4];
μ02s = [moment(c_ints[i], 2, c_avgs[i]) for i in 1:4];
μ20Ωs = [moment(n_vols[i], 2, n_vol_avgs[i]) for i in 1:4];
μ02Ωs = [moment(c_vols[i], 2, c_vol_avgs[i]) for i in 1:4];

In [17]:
μ20s_i = [μ20s[i] - ds[i]^2 * μ20Ωs[i] for i in 1:4]
μ02s_i = [μ02s[i] - bs[i]^2 * μ02Ωs[i] for i in 1:4];

Clearly the volume corrected means are simply the means if one averaged over the data. Can now store the values for the VC FF's along with the mean cyto #.

In [18]:
nuc_FFs = μ20s_i./vc_mean_ns

4-element Vector{Float64}:
 0.9558150606258131
 0.9926999917678184
 0.9744213797386199
 0.997142602245176

In [19]:
cyto_FFs = μ02s_i./vc_mean_cs

4-element Vector{Float64}:
 0.6129543833434689
 0.7557568194063666
 0.6613100531460392
 0.5879024967862935

In [20]:
cyto_means = vc_mean_cs

4-element Vector{Float64}:
 3.094988234996555
 2.668730143305501
 2.958044363335355
 2.610546234022334

# Now for the ABC...

In [21]:
using Random, Plots, LaTeXStrings, Distributions, StatsBase, DataFrames, CSV, Plots.PlotMeasures, Revise, GpABC, JLD2, FileIO

In [22]:
hypars = [3,3]; # [S,R]
# pf defined for the priors (see SI).
pf = (hypars[1]-1)/2

1.0

In [23]:
Plots.theme(:dao)
Plots.gr_cbar_width[] = 0.01;

In [24]:
Revise.track("/users/jamesh/GitHub/volume-inference-take-2/SSA-basic.jl")
include("/users/jamesh/GitHub/volume-inference-take-2/SSA-basic.jl")
using .SSAnonVD

In [25]:
pal = cgrad(:tol_muted);
cpal = [pal[i] for i in 1/7:1/7:1.0]
population_colors = cpal

In [26]:
tdeg = 1;
texpt(kA,kB,kC,S,R) = 1/kC;
tinit(kA,kB,kC,S,R) = (1/kB)+(S-1)/kA;

In [27]:
function sim_time(pars)
    kA, kB, kC = pars;
    return 10*maximum([1,texpt(pars...,hypars...),tinit(pars...,hypars...)])
end

sim_time (generic function with 1 method)

In [28]:
function new_distance(traj1::Matrix, traj2::Matrix)
    return sum([bs_vec[i]^(-1)*((traj1[i]-traj2[i])/traj2[i])^2 for i in 1:length(traj1)])
end
function new_distance(traj1::Vector, traj2::Vector)
    return sum([bs_vec[i]^(-1)*((traj1[i]-traj2[i])/traj2[i])^2 for i in 1:length(traj1)])
end

new_distance (generic function with 2 methods)

## Sample 1 of 4

In [29]:
sn = 1;
bs_vec = [0.00242,0.00171,0.00077];

In [30]:
function simulator_fn_1(pars)
    op = SSA(Ns[1], pars, hypars, sim_time(pars), sim_time(pars));
    nuc_pop = op[1][:,2];
    cyto_pop = op[2][:,2];
    nuc_FF = var(nuc_pop)/mean(nuc_pop);
    cyto_mean = 2*mean(cyto_pop);
    cyto_FF = var(cyto_pop)/mean(cyto_pop);
    # return the moments of interest
    return reshape([cyto_mean, nuc_FF, cyto_FF],(3,1))
end

simulator_fn_1 (generic function with 1 method)

Let's look at the value of the objective function for something close to an optimum value. This informs what our threshold schedule for the ABC will be.

In [31]:
new_distance(simulator_fn_1([2.54,3.64,20.0]),reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)))

51.97492856593203

In [32]:
# ABC priors
priors_1 = [Uniform(pf*0.5,pf*10.5), Uniform(0.5, 40.5), Uniform(20,220)]

# number of particles
n_particles = 1000

# ABC hpars
threshold_schedule_1 = [500.0,200.0,70.0,40.0,20.0,10.0,5.0,2.0,1.0]

8-element Vector{Float64}:
 500.0
 200.0
  70.0
  40.0
  20.0
  10.0
   5.0
   2.0

In [33]:
sim_abcsmc_res_1 = SimulatedABCSMC(reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)),
    simulator_fn_1,
    priors_1,
    threshold_schedule_1,
    n_particles; 
    max_iter=convert(Int, 1e5),
    distance_function = new_distance,
    write_progress=true);

[ Info: GpABC rejection simulation. ϵ = 500.0.
[ Info: GpABC rejection simulation. Accepted 763/1000 particles.
[ Info: GpABC SMC simulation ϵ = 200.0
[ Info: GpABC SMC simulation accepted 585/1000 particles.
[ Info: GpABC SMC simulation ϵ = 70.0
[ Info: GpABC SMC simulation accepted 376/1000 particles.
[ Info: GpABC SMC simulation accepted 777/2000 particles.
[ Info: GpABC SMC simulation ϵ = 40.0
[ Info: GpABC SMC simulation accepted 367/1000 particles.
[ Info: GpABC SMC simulation accepted 740/2000 particles.
[ Info: GpABC SMC simulation ϵ = 20.0
[ Info: GpABC SMC simulation accepted 285/1000 particles.
[ Info: GpABC SMC simulation accepted 579/2000 particles.
[ Info: GpABC SMC simulation accepted 868/3000 particles.
[ Info: GpABC SMC simulation ϵ = 10.0
[ Info: GpABC SMC simulation accepted 270/1000 particles.
[ Info: GpABC SMC simulation accepted 502/2000 particles.
[ Info: GpABC SMC simulation accepted 749/3000 particles.
[ Info: GpABC SMC simulation ϵ = 5.0
[ Info: GpABC SMC simu

In [34]:
plot(sim_abcsmc_res_1)

In [35]:
save("./jld2-res/S$(hypars[1])R$(hypars[2])_mad1WTGFP_samp1.jld2", "ABC", sim_abcsmc_res_1)

## Sample 2 of 4

In [36]:
sn = 2;
bs_vec = [0.00169,0.00109,0.00109];

In [37]:
function simulator_fn_2(pars)
    op = SSA(Ns[2], pars, hypars, sim_time(pars), sim_time(pars));
    nuc_pop = op[1][:,2];
    cyto_pop = op[2][:,2];
    nuc_FF = var(nuc_pop)/mean(nuc_pop);
    cyto_mean = 2*mean(cyto_pop);
    cyto_FF = var(cyto_pop)/mean(cyto_pop);
    # return the moments of interest
    return reshape([cyto_mean, nuc_FF, cyto_FF],(3,1))
end

simulator_fn_2 (generic function with 1 method)

Let's look at the value of the objective function for something close to an optimum value. This informs what our threshold schedule for the ABC will be.

In [38]:
new_distance(simulator_fn_2([2.54,3.64,20.0]),reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)))

93.02934647248472

In [39]:
# ABC priors
priors_2 = [Uniform(pf*0.5,pf*10.5), Uniform(0.5, 40.5), Uniform(20,220)]

# number of particles
n_particles = 1000

# ABC hpars
threshold_schedule_2 = [500.0,200.0,70.0,40.0,20.0,10.0,5.0,2.0]

8-element Vector{Float64}:
 500.0
 200.0
  70.0
  40.0
  20.0
  10.0
   5.0
   2.0

In [ ]:
sim_abcsmc_res_2 = SimulatedABCSMC(reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)),
    simulator_fn_2,
    priors_2,
    threshold_schedule_2,
    n_particles; 
    max_iter=convert(Int, 1e5),
    distance_function = new_distance,
    write_progress=true);

[ Info: GpABC rejection simulation. ϵ = 500.0.
[ Info: GpABC rejection simulation. Accepted 605/1000 particles.
[ Info: GpABC SMC simulation ϵ = 200.0
[ Info: GpABC SMC simulation accepted 499/1000 particles.


In [ ]:
plot(sim_abcsmc_res_2)

In [ ]:
save("./jld2-res/S$(hypars[1])R$(hypars[2])_mad1WTGFP_samp2.jld2", "ABC", sim_abcsmc_res_2)

## Sample 3 of 4

In [ ]:
sn = 3;
bs_vec = [0.00135,0.00079,0.00049];

In [ ]:
function simulator_fn_3(pars)
    op = SSA(Ns[3], pars, hypars, sim_time(pars), sim_time(pars));
    nuc_pop = op[1][:,2];
    cyto_pop = op[2][:,2];
    nuc_FF = var(nuc_pop)/mean(nuc_pop);
    cyto_mean = 2*mean(cyto_pop);
    cyto_FF = var(cyto_pop)/mean(cyto_pop);
    # return the moments of interest
    return reshape([cyto_mean, nuc_FF, cyto_FF],(3,1))
end

Let's look at the value of the objective function for something close to an optimum value. This informs what our threshold schedule for the ABC will be.

In [ ]:
new_distance(simulator_fn_3([2.54,3.64,20.0]),reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)))

In [ ]:
# ABC priors
priors_3 = [Uniform(pf*0.5,pf*10.5), Uniform(0.5, 40.5), Uniform(20,220)]

# number of particles
n_particles = 1000

# ABC hpars
threshold_schedule_3 = [500.0,200.0,70.0,40.0,20.0,10.0,5.0,2.0]

In [ ]:
sim_abcsmc_res_3 = SimulatedABCSMC(reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)),
    simulator_fn_3,
    priors_3,
    threshold_schedule_3,
    n_particles; 
    max_iter=convert(Int, 1e5),
    distance_function = new_distance,
    write_progress=true);

In [ ]:
plot(sim_abcsmc_res_3)

In [ ]:
save("./jld2-res/S$(hypars[1])R$(hypars[2])_mad1WTGFP_samp3.jld2", "ABC", sim_abcsmc_res_3)

## Sample 4 of 4

In [ ]:
sn = 4;
bs_vec = [0.001099,0.001136,0.000364];

In [ ]:
function simulator_fn_4(pars)
    op = SSA(Ns[4], pars, hypars, sim_time(pars), sim_time(pars));
    nuc_pop = op[1][:,2];
    cyto_pop = op[2][:,2];
    nuc_FF = var(nuc_pop)/mean(nuc_pop);
    cyto_mean = 2*mean(cyto_pop);
    cyto_FF = var(cyto_pop)/mean(cyto_pop);
    # return the moments of interest
    return reshape([cyto_mean, nuc_FF, cyto_FF],(3,1))
end

Let's look at the value of the objective function for something close to an optimum value. This informs what our threshold schedule for the ABC will be.

In [ ]:
new_distance(simulator_fn_1([2.54,3.64,20.0]),reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)))

In [ ]:
# ABC priors
priors_4 = [Uniform(pf*0.5,pf*10.5), Uniform(0.5, 40.5), Uniform(20,220)]

# number of particles
n_particles = 1000

# ABC hpars
threshold_schedule_4 = [500.0,200.0,70.0,40.0,20.0,10.0,5.0,2.0]

In [ ]:
sim_abcsmc_res_4 = SimulatedABCSMC(reshape([cyto_means[sn],nuc_FFs[sn],cyto_FFs[sn]],(3,1)),
    simulator_fn_4,
    priors_4,
    threshold_schedule_4,
    n_particles; 
    max_iter=convert(Int, 1e5),
    distance_function = new_distance,
    write_progress=true);

In [ ]:
plot(sim_abcsmc_res_4)

In [ ]:
save("./jld2-res/S$(hypars[1])R$(hypars[2])_mad1WTGFP_samp4.jld2", "ABC", sim_abcsmc_res_4)